In [1]:
import requests

electionId = "103"  

url = "https://backend.smartvote.ch/api/graphql"
headers = {}

# First query - Get candidates and their answers (keep your existing query)
candidate_query = {
    "operationName": "SearchCandidates",
    "variables": {"searchParams": {"electionId": electionId}},
    "query": """
    query SearchCandidates($searchParams: CandidateSearchParams!) {
        candidates(searchParams: $searchParams) {
            ...SearchCandidate
        }
    }

    fragment SearchCandidate on Candidate {
        id
        firstname
        lastname
        yearOfBirth
        profileImageUrl
        isIncumbent
        isElected
        partyAbbreviation
        partyColor
        hasSmartvoteProfile
        gender

        answers {
            ...Answer
        }
    }

    fragment Answer on Answer {
        questionId
        value
    }
    """,
}

# Second query - Get questions details
question_query = {
    "operationName": "GetElectionQuestions",
    "variables": {"electionId": electionId},
    "query": """
    query GetElectionQuestions($electionId: ID!) {
      election(id: $electionId) {
        questionnaire {
          categories {
            id
            name
            description
            questions {
              id
              text
              sortorder
              pro
              contra
              info
              type
              isInRapide
            }
          }
        }
      }
    }
    """
}

# Execute both queries
candidate_response = requests.post(url, headers=headers, json=candidate_query)
question_response = requests.post(url, headers=headers, json=question_query)

# Store the results
candidate_data = candidate_response.json()
question_data = question_response.json()

# Print candidate response for backward compatibility with your existing code
print(candidate_data)

# Also print confirmation of question data retrieval
print(f"Retrieved questionnaire data for election {electionId}")

{'data': {'candidates': [{'id': '18762', 'firstname': 'Antonio', 'lastname': 'Abate', 'yearOfBirth': 1967, 'profileImageUrl': 'https://backend.smartvote.ch/rails/active_storage/blobs/redirect/eyJfcmFpbHMiOnsiZGF0YSI6MjQ2MDYsInB1ciI6ImJsb2JfaWQifX0=--d5bfc75a3430c03e0ed160b8c8ae64dd0caeaffa/9aefd014-2410-4d32-bbd9-b3e0e207e2cc.jpeg', 'isIncumbent': False, 'isElected': False, 'partyAbbreviation': 'Die Mitte', 'partyColor': '#FF9B00', 'hasSmartvoteProfile': True, 'gender': 'm', 'answers': [{'questionId': '5156', 'value': 25}, {'questionId': '5158', 'value': 75}, {'questionId': '5160', 'value': 25}, {'questionId': '5162', 'value': 25}, {'questionId': '5164', 'value': 100}, {'questionId': '5166', 'value': 75}, {'questionId': '5168', 'value': 75}, {'questionId': '5170', 'value': 25}, {'questionId': '5172', 'value': 100}, {'questionId': '5174', 'value': 100}, {'questionId': '5176', 'value': 100}, {'questionId': '5178', 'value': 100}, {'questionId': '5180', 'value': 100}, {'questionId': '5182'

In [2]:
candidates = candidate_response.json()["data"]["candidates"]
print(f"Length: {len(candidates)} candidate(s)")

Length: 2214 candidate(s)


In [3]:
print(candidates[102])

{'id': '19542', 'firstname': 'Albert', 'lastname': 'Bach-Tiemer', 'yearOfBirth': 1959, 'profileImageUrl': None, 'isIncumbent': False, 'isElected': False, 'partyAbbreviation': 'SVP', 'partyColor': '#0A7228', 'hasSmartvoteProfile': True, 'gender': 'm', 'answers': [{'questionId': '5156', 'value': 100}, {'questionId': '5158', 'value': 25}, {'questionId': '5160', 'value': 75}, {'questionId': '5162', 'value': 0}, {'questionId': '5164', 'value': 25}, {'questionId': '5166', 'value': 0}, {'questionId': '5168', 'value': 75}, {'questionId': '5170', 'value': 0}, {'questionId': '5172', 'value': 0}, {'questionId': '5174', 'value': 100}, {'questionId': '5176', 'value': 0}, {'questionId': '5178', 'value': 25}, {'questionId': '5180', 'value': 0}, {'questionId': '5182', 'value': 0}, {'questionId': '5184', 'value': 75}, {'questionId': '5186', 'value': 25}, {'questionId': '5188', 'value': 25}, {'questionId': '5190', 'value': 0}, {'questionId': '5192', 'value': 100}, {'questionId': '5194', 'value': 100}, {

clean up the data so 'hasSmartvoteProfile': True


In [4]:
filtered_candidates = [candidate for candidate in candidates if candidate['hasSmartvoteProfile']]

print(f"Length: {len(filtered_candidates)} candidate(s) with smartvote profile")

Length: 1877 candidate(s) with smartvote profile


In [5]:
# Process question data to create a mapping of question IDs to details
question_map = {}

# Check if we have a valid response
if "data" in question_data and question_data["data"]["election"] and question_data["data"]["election"]["questionnaire"]:
    categories = question_data["data"]["election"]["questionnaire"]["categories"]
    
    for category in categories:
        category_name = category["name"]
        for question in category["questions"]:
            question_map[question["id"]] = {
                "text": question["text"],
                "category": category_name,
                "pro": question["pro"],
                "contra": question["contra"],
                "type": question["type"]
            }
    
    print(f"Processed {len(question_map)} questions from {len(categories)} categories")
else:
    print("Failed to retrieve question data or unexpected response format")

Processed 58 questions from 13 categories


In [6]:
import pandas as pd
import json

# Create a copy of filtered candidates for enhancing with question data
enhanced_candidates = []

for candidate in filtered_candidates:
    # Create a copy of the candidate data
    enhanced_candidate = candidate.copy()
    
    # Get the answers as Python objects
    if 'answers' in candidate:
        if isinstance(candidate['answers'], str):
            answers = json.loads(candidate['answers'])
        else:
            answers = candidate['answers']
        
        # Enhance answers with question text
        enhanced_answers = []
        for answer in answers:
            q_id = answer["questionId"]
            enhanced_answer = answer.copy()
            
            if q_id in question_map:
                enhanced_answer["questionText"] = question_map[q_id]["text"]
                enhanced_answer["category"] = question_map[q_id]["category"]
            else:
                enhanced_answer["questionText"] = "Unknown question"
                enhanced_answer["category"] = "Unknown category"
                
            enhanced_answers.append(enhanced_answer)
        
        # Store both formats
        enhanced_candidate['answers'] = json.dumps(answers)  # Original format
        enhanced_candidate['enhanced_answers'] = json.dumps(enhanced_answers)  # Enhanced format
    
    enhanced_candidates.append(enhanced_candidate)

# Create and export DataFrames
candidate_df = pd.DataFrame(enhanced_candidates)
enhanced_csv_filename = 'candidates_with_questions.csv'
candidate_df.to_csv(enhanced_csv_filename, index=False)
print(f"Enhanced candidate data exported to {enhanced_csv_filename}")

# Also export questions as a separate CSV for reference
questions_list = [{"id": qid, **details} for qid, details in question_map.items()]
questions_df = pd.DataFrame(questions_list)
questions_csv = 'questions.csv'
questions_df.to_csv(questions_csv, index=False)
print(f"Questions data exported to {questions_csv}")

Enhanced candidate data exported to candidates_with_questions.csv
Questions data exported to questions.csv
